In [ ]:
# !pip install opencv-python onnxruntime-gpu insightface selenium

In [10]:
import os
import cv2
import json
import requests
import numpy as np
from PIL import Image
from io import BytesIO
import insightface
import time
import random
from skimage import transform as trans

In [ ]:
# init insightface
model = insightface.app.FaceAnalysis(name='buffalo_l', providers=['CPUExecutionProvider'])
model.prepare(ctx_id=0)

Applied providers: ['CPUExecutionProvider'], with options: {'CPUExecutionProvider': {}}
find model: /home/shuof/.insightface/models/buffalo_l/1k3d68.onnx landmark_3d_68 ['None', 3, 192, 192] 0.0 1.0
Applied providers: ['CPUExecutionProvider'], with options: {'CPUExecutionProvider': {}}
find model: /home/shuof/.insightface/models/buffalo_l/2d106det.onnx landmark_2d_106 ['None', 3, 192, 192] 0.0 1.0
Applied providers: ['CPUExecutionProvider'], with options: {'CPUExecutionProvider': {}}
find model: /home/shuof/.insightface/models/buffalo_l/det_10g.onnx detection [1, 3, '?', '?'] 127.5 128.0
Applied providers: ['CPUExecutionProvider'], with options: {'CPUExecutionProvider': {}}
find model: /home/shuof/.insightface/models/buffalo_l/genderage.onnx genderage ['None', 3, 96, 96] 0.0 1.0
Applied providers: ['CPUExecutionProvider'], with options: {'CPUExecutionProvider': {}}
find model: /home/shuof/.insightface/models/buffalo_l/w600k_r50.onnx recognition ['None', 3, 112, 112] 127.5 127.5
set det

In [ ]:
def is_clear_and_frontal(landmarks, face_box, aligned_img):
    left_eye, right_eye = landmarks[0], landmarks[1]
    dx = abs(left_eye[0] - right_eye[0])
    dy = abs(left_eye[1] - right_eye[1])
    slope = dy / (dx + 1e-6)

    # 1. 眼睛是否水平（避免側臉或歪頭）
    if slope > 0.08:  # 原本是 0.15，現在更嚴格
        return False

    # 2. 左右眼距離與臉寬一致性（避免歪頭導致的錯位）
    eye_dist = np.linalg.norm(np.array(left_eye) - np.array(right_eye))
    box_w = face_box[2] - face_box[0]
    ratio = eye_dist / (box_w + 1e-6)
    if ratio < 0.35 or ratio > 0.6:  # 避免太窄或太開（側臉會異常）
        return False

    # 3. 臉大小過小不要
    if box_w < 80 or (face_box[3] - face_box[1]) < 80:
        return False

    # 4. 模糊度檢查
    gray = cv2.cvtColor(aligned_img, cv2.COLOR_RGB2GRAY)
    lap_var = cv2.Laplacian(gray, cv2.CV_64F).var()
    if lap_var < 50:
        return False

    return True

def process_images_from_json_urls(json_path, output_dir):
    os.makedirs(output_dir, exist_ok=True)

    #  從現有檔案找起始編號
    current_id = get_next_id(output_dir)

    with open(json_path, 'r', encoding='utf-8') as f:
        data = json.load(f)
        image_urls = data.get("image_urls", [])

    total_saved = 0
    for i, url in enumerate(image_urls):
        saved, current_id = extract_from_url(url, output_dir, current_id)
        print(f"[✓] 第 {i+1} 張圖：儲存 {saved} 張人臉")
        total_saved += saved

    print(f"\n🎯 全部完成，共儲存 {total_saved} 張人臉圖")

def face_align(img_rgb, landmarks, shift_y=10, output_size=140):

    # 標準五點（arcface 格式）
    src = np.array([
        [30.2946, 51.6963],
        [65.5318, 51.5014],
        [48.0252, 71.7366],
        [33.5493, 92.3655],
        [62.7299, 92.2041],
    ], dtype=np.float32)

    src[:, 1] += shift_y

    dst = np.array(landmarks, dtype=np.float32).reshape(5, 2)
    tform = trans.SimilarityTransform()
    tform.estimate(dst, src)
    M = tform.params[0:2, :]

    aligned = cv2.warpAffine(img_rgb, M, (output_size, output_size), borderValue=0)
    return aligned

def get_next_id(output_dir):
    """從資料夾中找出目前最大檔名編號，回傳下一個起始編號"""
    existing_files = os.listdir(output_dir)
    ids = []
    for fname in existing_files:
        if fname.endswith(".png"):
            try:
                ids.append(int(os.path.splitext(fname)[0]))
            except:
                continue
    return max(ids) + 1 if ids else 0

def download_image_with_headers(url, max_retry=2):
    headers = {
        'User-Agent': 'Mozilla/5.0',
        'Referer': 'https://imgur.com/'
    }

    for attempt in range(max_retry):
        try:
            print(f"[↓] 嘗試下載圖片（第 {attempt+1} 次）：{url}")
            response = requests.get(url, headers=headers, timeout=10)
            if response.status_code == 200:
                return Image.open(BytesIO(response.content)).convert("RGB")
            else:
                print(f"[!] 狀態碼 {response.status_code}，來自：{url}")
        except Exception as e:
            print(f"[X] 嘗試錯誤：{e}")
        time.sleep(random.uniform(2, 5))
    return None

def extract_from_url(url, output_dir, start_id=0, resize_size=64):
    img = download_image_with_headers(url)
    if img is None:
        print(f"[X] 無法下載圖片：{url}")
        return 0, start_id

    try:
        img_bgr = cv2.cvtColor(np.array(img), cv2.COLOR_RGB2BGR)
    except Exception as e:
        print(f"[X] 圖片格式錯誤或轉換失敗：{url}，錯誤訊息：{e}")
        return 0, start_id

    faces = model.get(img_bgr)
    saved_count = 0
    img_rgb = cv2.cvtColor(img_bgr, cv2.COLOR_BGR2RGB)

    current_id = start_id

    for idx, face in enumerate(faces):
        box = face.bbox.astype(int)
        landmarks = face.kps

        aligned = face_align(img_rgb, landmarks, shift_y=10, output_size=140)
        resized = cv2.resize(aligned, (resize_size, resize_size))

        if is_clear_and_frontal(landmarks, box, aligned):
            out_path = os.path.join(output_dir, f"{current_id}.png")
            cv2.imwrite(out_path, cv2.cvtColor(resized, cv2.COLOR_RGB2BGR))
            saved_count += 1
            current_id += 1  # 編號 +1

    return saved_count, current_id

In [ ]:
process_images_from_json_urls(
    "all_images_0101_1231.json",
    "./2024"
)

[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/eTUa7QK.jpg
[✓] 第 1 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/JG146Eb.jpg
[✓] 第 2 張圖：儲存 1 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/iONhv6s.jpg
[✓] 第 3 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/nszQumU.jpg
[✓] 第 4 張圖：儲存 1 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/XQed8sr.jpg
[✓] 第 5 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/r2W7UAb.jpg
[✓] 第 6 張圖：儲存 1 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/7thDeA1.jpg
[✓] 第 7 張圖：儲存 1 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/ftE9xOo.jpg
[✓] 第 8 張圖：儲存 1 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/h3NmnQG.jpg
[✓] 第 9 張圖：儲存 1 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/ZHacaPh.jpg
[✓] 第 10 張圖：儲存 1 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/F1rACDx.jpg
[✓] 第 11 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/klOc5Hi.jpg
[✓] 第 12 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/RRD8uXx.jpg
[✓] 第 13 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/BrLUXUe.jpg
[✓] 第 14 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 

/home/shuof/.conda/envs/crawl/lib/python3.12/site-packages/PIL/Image.py:1043: UserWarning: Palette images with Transparency expressed in bytes should be converted to RGBA images
  warnings.warn(


[✓] 第 6629 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/jo20ZB7.jpg
[✓] 第 6630 張圖：儲存 2 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/22BAUf8.jpg
[✓] 第 6631 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/TyfboPt.jpg
[✓] 第 6632 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/nmvHyTK.jpg
[✓] 第 6633 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/xCBetZJ.jpg
[✓] 第 6634 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/ue4Suaq.jpg
[✓] 第 6635 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/DqbIhOK.jpg
[✓] 第 6636 張圖：儲存 1 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/g4MC981.jpg
[✓] 第 6637 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/CFa6Sui.jpg
[✓] 第 6638 張圖：儲存 1 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/zcIxPGy.jpg
[✓] 第 6639 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：https://i.imgur.com/ndT5e41.jpg
[✓] 第 6640 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：http://i.imgur.com/sg5Ynw5.jpg
[✓] 第 6641 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：http://i.imgur.com/tq0VaPH.jpg
[✓] 第 6642 張圖：儲存 0 張人臉
[↓] 嘗試下載圖片（第 1 次）：http://i.img